In [0]:
import pandas as pd 
from pyspark.sql.functions import pandas_udf, col, PandasUDFType
from pyspark.sql.types import IntegerType
from typing import Iterator, Tuple

In [0]:
# make sure that com.azure.cosmos.spark additional library is being installed on cluster as in tutorial
# note that it's not safe to store credentials (endpoint, key) in code, as below. It's recomended to create secrets in Azure Key Vault instead

cosmosEndpoint = "https://my-cosmos-db-account.documents.azure.com:443/"
cosmosMasterKey = "FyumkXMjoTgoB9mEXHGhweChrVgRe9As4gd6TtN17c5e4tlGWy18e9NjegAm3L07ceVE6BJ9KTymACDbJUvXIQ=="
cosmosDatabaseName = "superstore_db"
cosmosContainerName = "superstore-container"

cfg = {
    "spark.cosmos.accountEndpoint": cosmosEndpoint,
    "spark.cosmos.accountKey": cosmosMasterKey,
    "spark.cosmos.database": cosmosDatabaseName,
    "spark.cosmos.container": cosmosContainerName
}

In [0]:
spark.conf.set("spark.sql.catalog.cosmosCatalog", "com.azure.cosmos.spark.CosmosCatalog")
spark.conf.set("spark.sql.catalog.cosmosCatalog.spark.cosmos.accountEndpoint", cosmosEndpoint)
spark.conf.set("spark.sql.catalog.cosmosCatalog.spark.cosmos.accountKey", cosmosMasterKey)

In [0]:
from pyspark.sql.functions import col
superstore_df = spark.read.format("cosmos.oltp").options(**cfg)\
                          .option("spark.cosmos.read.inferSchema.enabled", "true")\
                          .load()

In [0]:
# create vectorized UDF

def year(date: pd.Series) -> pd.Series:
    return pd.to_datetime(date).dt.year

year_pandas = pandas_udf(year, returnType=IntegerType())

In [0]:
superstore_df.withColumn('Year', year_pandas(col('Order Date')))\
             .select('Order Date', 'Category', 'Year').display()

Order Date Category Year 7/16/2017 Furniture 2017 9/17/2015 Office Supplies 2015 7/17/2016 Office Supplies 2016 9/19/2017 Office Supplies 2017 10/20/2014 Office Supplies 2014 4/18/2015 Furniture 2015 6/4/2016 Office Supplies 2016 11/26/2014 Furniture 2014 6/12/2016 Office Supplies 2016 6/12/2016 Furniture 2016 5/31/2015 Office Supplies 2015 5/31/2015 Office Supplies 2015 12/5/2014 Office Supplies 2014 8/26/2014 Technology 2014 7/16/2016 Office Supplies 2016 10/12/2015 Office Supplies 2015 7/6/2017 Office Supplies 2017 12/9/2017 Technology 2017 12/24/2015 Office Supplies 2015 6/4/2016 Furniture 2016 9/11/2016 Office Supplies 2016 11/28/2015 Office Supplies 2015 11/28/2015 Office Supplies 2015 9/19/2014 Technology 2014 6/16/2017 Office Supplies 2017 11/2/2015 Furniture 2015 12/18/2016 Office Supplies 2016 12/18/2016 Office Supplies 2016 11/20/2016 Office Supplies 2016 8/30/2016 Office Supplies 2016 4/25/2016 Office Supplies 2016 4/13/2014 Office Supplies 2014 6/15/2017 Technology 2017 9/24/2014 Office Supplies 2014 12/3/2015 Furniture 2015 12/11/2017 Technology 2017 6/7/2014 Office Supplies 2014 12/24/2014 Office Supplies 2014 12/8/2017 Technology 2017 12/8/2017 Furniture 2017 10/19/2017 Furniture 2017 9/12/2014 Technology 2014 3/20/2017 Furniture 2017 10/20/2017 Furniture 2017 12/13/2016 Technology 2016 4/22/2016 Furniture 2016 11/9/2014 Office Supplies 2014 10/27/2016 Furniture 2016 10/6/2014 Technology 2014 9/14/2014 Office Supplies 2014 12/27/2015 Office Supplies 2015 10/20/2016 Office Supplies 2016 5/21/2016 Technology 2016 5/29/2016 Technology 2016 12/3/2015 Office Supplies 2015 12/7/2015 Office Supplies 2015 12/18/2015 Office Supplies 2015 5/11/2014 Furniture 2014 4/15/2016 Furniture 2016 11/20/2017 Office Supplies 2017 9/14/2014 Furniture 2014 12/7/2015 Office Supplies 2015 9/10/2015 Office Supplies 2015 1/9/2014 Office Supplies 2014 8/8/2014 Technology 2014 5/23/2014 Office Supplies 2014 8/18/2017 Furniture 2017 11/29/2015 Office Supplies 2015 4/1/2016 Office Supplies 2016 12/11/2016 Furniture 2016 12/11/2016 Technology 2016 6/19/2017 Technology 2017 11/19/2016 Office Supplies 2016 7/5/2014 Office Supplies 2014 9/2/2017 Furniture 2017 11/4/2016 Furniture 2016 2/13/2016 Office Supplies 2016 12/15/2016 Furniture 2016 12/3/2016 Office Supplies 2016 1/21/2017 Office Supplies 2017 10/2/2017 Furniture 2017 2/8/2015 Technology 2015 1/30/2017 Furniture 2017 10/3/2015 Office Supplies 2015 10/3/2015 Furniture 2015 12/12/2015 Furniture 2015 3/12/2016 Office Supplies 2016 2/3/2015 Furniture 2015 10/13/2014 Office Supplies 2014 10/13/2014 Technology 2014 6/16/2017 Office Supplies 2017 11/20/2015 Furniture 2015 11/7/2016 Office Supplies 2016 6/20/2016 Office Supplies 2016 6/9/2014 Office Supplies 2014 1/5/2016 Technology 2016 4/29/2014 Furniture 2014 11/10/2016 Office Supplies 2016 11/10/2016 Office Supplies 2016 10/5/2015 Office Supplies 2015 4/14/2017 Office Supplies 2017 12/13/2015 Office Supplies 2015 11/28/2017 Furniture 2017 11/28/2017 Office Supplies 2017 5/15/2017 Office Supplies 2017 9/22/2015 Furniture 2015 9/22/2014 Office Supplies 2014 4/9/2017 Office Supplies 2017 1/16/2014 Technology 2014 1/16/2014 Office Supplies 2014 1/16/2014 Office Supplies 2014 12/9/2015 Office Supplies 2015 11/11/2014 Technology 2014 9/9/2016 Office Supplies 2016 10/28/2015 Furniture 2015 4/27/2015 Technology 2015 10/12/2017 Furniture 2017 3/8/2016 Technology 2016 11/24/2016 Office Supplies 2016 4/16/2015 Office Supplies 2015 4/16/2015 Office Supplies 2015 7/25/2015 Office Supplies 2015 11/29/2015 Office Supplies 2015 3/1/2016 Office Supplies 2016 12/6/2015 Technology 2015 11/19/2016 Office Supplies 2016 11/19/2016 Office Supplies 2016 9/4/2015 Technology 2015 1/20/2014 Technology 2014 12/31/2016 Office Supplies 2016 12/20/2014 Furniture 2014 12/8/2017 Office Supplies 2017 12/1/2016 Furniture 2016 7/18/2016 Office Supplies 2016 12/4/2016 Office Supplies 2016 10/31/2015 Office Supplies 2015 10/28/2016 Furniture 2016 10/28/2016 Furniture 2016 12/24/

In [0]:
# it is preffered to use anotations to create vectorized (same as usual) UDFs
# annotation "year(date: pd.Series) -> pd.Series:" gives python hints what type of data in/out

@pandas_udf('integer', PandasUDFType.SCALAR)
def year(date: pd.Series) -> pd.Series:
    return pd.to_datetime(date).dt.year

@pandas_udf('integer', PandasUDFType.SCALAR)
def month(date: pd.Series) -> pd.Series:
    return pd.to_datetime(date).dt.month

@pandas_udf('integer', PandasUDFType.SCALAR)
def day(date: pd.Series) -> pd.Series:
    return pd.to_datetime(date).dt.day

/databricks/spark/python/pyspark/sql/pandas/functions.py:386: UserWarning: In Python 3.6+ and Spark 3.0+, it is preferred to specify type hints for pandas UDF instead of specifying pandas UDF type which will be deprecated in the future releases. See SPARK-28264 for more details.
 warnings.warn(

In [0]:
superstore_df.withColumn('Year', year(col('Order Date')))\
             .withColumn('Month', month(col('Order Date')))\
             .withColumn('Day', day(col('Order Date')))\
             .select('Category', 'Order Date', 'Year', 'Month', 'Day').display()

Category Order Date Year Month Day Furniture 7/16/2017 2017 7 16 Office Supplies 9/17/2015 2015 9 17 Office Supplies 7/17/2016 2016 7 17 Office Supplies 9/19/2017 2017 9 19 Office Supplies 10/20/2014 2014 10 20 Furniture 4/18/2015 2015 4 18 Office Supplies 6/4/2016 2016 6 4 Furniture 11/26/2014 2014 11 26 Office Supplies 6/12/2016 2016 6 12 Furniture 6/12/2016 2016 6 12 Office Supplies 5/31/2015 2015 5 31 Office Supplies 5/31/2015 2015 5 31 Office Supplies 12/5/2014 2014 12 5 Technology 8/26/2014 2014 8 26 Office Supplies 7/16/2016 2016 7 16 Office Supplies 10/12/2015 2015 10 12 Office Supplies 7/6/2017 2017 7 6 Technology 12/9/2017 2017 12 9 Office Supplies 12/24/2015 2015 12 24 Furniture 6/4/2016 2016 6 4 Office Supplies 9/11/2016 2016 9 11 Office Supplies 11/28/2015 2015 11 28 Office Supplies 11/28/2015 2015 11 28 Technology 9/19/2014 2014 9 19 Office Supplies 6/16/2017 2017 6 16 Furniture 11/2/2015 2015 11 2 Office Supplies 12/18/2016 2016 12 18 Office Supplies 12/18/2016 2016 12 18 Office Supplies 11/20/2016 2016 11 20 Office Supplies 8/30/2016 2016 8 30 Office Supplies 4/25/2016 2016 4 25 Office Supplies 4/13/2014 2014 4 13 Technology 6/15/2017 2017 6 15 Office Supplies 9/24/2014 2014 9 24 Furniture 12/3/2015 2015 12 3 Technology 12/11/2017 2017 12 11 Office Supplies 6/7/2014 2014 6 7 Office Supplies 12/24/2014 2014 12 24 Technology 12/8/2017 2017 12 8 Furniture 12/8/2017 2017 12 8 Furniture 10/19/2017 2017 10 19 Technology 9/12/2014 2014 9 12 Furniture 3/20/2017 2017 3 20 Furniture 10/20/2017 2017 10 20 Technology 12/13/2016 2016 12 13 Furniture 4/22/2016 2016 4 22 Office Supplies 11/9/2014 2014 11 9 Furniture 10/27/2016 2016 10 27 Technology 10/6/2014 2014 10 6 Office Supplies 9/14/2014 2014 9 14 Office Supplies 12/27/2015 2015 12 27 Office Supplies 10/20/2016 2016 10 20 Technology 5/21/2016 2016 5 21 Technology 5/29/2016 2016 5 29 Office Supplies 12/3/2015 2015 12 3 Office Supplies 12/7/2015 2015 12 7 Office Supplies 12/18/2015 2015 12 18 Furniture 5/11/2014 2014 5 11 Furniture 4/15/2016 2016 4 15 Office Supplies 11/20/2017 2017 11 20 Furniture 9/14/2014 2014 9 14 Office Supplies 12/7/2015 2015 12 7 Office Supplies 9/10/2015 2015 9 10 Office Supplies 1/9/2014 2014 1 9 Technology 8/8/2014 2014 8 8 Office Supplies 5/23/2014 2014 5 23 Furniture 8/18/2017 2017 8 18 Office Supplies 11/29/2015 2015 11 29 Office Supplies 4/1/2016 2016 4 1 Furniture 12/11/2016 2016 12 11 Technology 12/11/2016 2016 12 11 Technology 6/19/2017 2017 6 19 Office Supplies 11/19/2016 2016 11 19 Office Supplies 7/5/2014 2014 7 5 Furniture 9/2/2017 2017 9 2 Furniture 11/4/2016 2016 11 4 Office Supplies 2/13/2016 2016 2 13 Furniture 12/15/2016 2016 12 15 Office Supplies 12/3/2016 2016 12 3 Office Supplies 1/21/2017 2017 1 21 Furniture 10/2/2017 2017 10 2 Technology 2/8/2015 2015 2 8 Furniture 1/30/2017 2017 1 30 Office Supplies 10/3/2015 2015 10 3 Furniture 10/3/2015 2015 10 3 Furniture 12/12/2015 2015 12 12 Office Supplies 3/12/2016 2016 3 12 Furniture 2/3/2015 2015 2 3 Office Supplies 10/13/2014 2014 10 13 Technology 10/13/2014 2014 10 13 Office Supplies 6/16/2017 2017 6 16 Furniture 11/20/2015 2015 11 20 Office Supplies 11/7/2016 2016 11 7 Office Supplies 6/20/2016 2016 6 20 Office Supplies 6/9/2014 2014 6 9 Technology 1/5/2016 2016 1 5 Furniture 4/29/2014 2014 4 29 Office Supplies 11/10/2016 2016 11 10 Office Supplies 11/10/2016 2016 11 10 Office Supplies 10/5/2015 2015 10 5 Office Supplies 4/14/2017 2017 4 14 Office Supplies 12/13/2015 2015 12 13 Furniture 11/28/2017 2017 11 28 Office Supplies 11/28/2017 2017 11 28 Office Supplies 5/15/2017 2017 5 15 Furniture 9/22/2015 2015 9 22 Office Supplies 9/22/2014 2014 9 22 Office Supplies 4/9/2017 2017 4 9 Technology 1/16/2014 2014 1 16 Office Supplies 1/16/2014 2014 1 16 Office Supplies 1/16/2014 2014 1 16 Office Supplies 12/9/2015 2015 12 9 Technology 11/11/2014 2014 11 11 Office Supplies 9/9/2016 2016 9 9 Furniture 10/28/2015 2015 10 28 Technology 4/27/2015 2015 4 27 Furniture 10/12/2017 2017 10 12 Tec

In [0]:
@pandas_udf('first string, last string')
def firstname_lastname(name: pd.Series) ->pd.Series:
    return name.str.split(expand=True)

In [0]:
superstore_df.select(firstname_lastname('Customer Name')).display()

firstname_lastname(Customer Name) List(Sandra, Flanagan) List(Tracy, Blumstein) List(Ruben, Ausman) List(Erin, Smith) List(Patrick, O'Donnell) List(Darren, Powers) List(Karen, Daniels) List(Joel, Eaton) List(Stewart, Carmichael) List(Steven, Cartwright) List(Stephanie, Phelps) List(Stephanie, Phelps) List(David, Kendrick) List(Frank, Merwin) List(Alice, McCarthy) List(Mark, Packer) List(Fred, Hopkins) List(Laurel, Elliston) List(Joni, Blumstein) List(Ken, Lonsdale) List(Kelly, Collister) List(Dan, Reichenbach) List(Dan, Reichenbach) List(Sean, Braxton) List(Claudia, Bergmann) List(Jas, O'Carroll) List(Alan, Haines) List(Alan, Haines) List(Nick, Zandusky) List(Patrick, O'Brill) List(John, Lucas) List(Jonathan, Doherty) List(Clay, Cheatham) List(Julia, Dunbar) List(Dean, Katz) List(Mike, Vittorini) List(Bart, Pistole) List(Luke, Foster) List(Keith, Herrera) List(Keith, Herrera) List(Michael, Paige) List(Shirley, Daniels) List(Troy, Blackwell) List(Ed, Braxton) List(Ken, Heidel) List(Tanja, Norvell) List(Jeremy, Pistek) List(Jeremy, Ellison) List(Xylona, Preis) List(Astrea, Jones) List(Maribeth, Dona) List(Luke, Foster) List(Logan, Haushalter) List(Rob, Lucas) List(Mark, Packer) List(Darren, Koutras) List(Liz, MacKendrick) List(Paul, Gonzalez) List(Bill, Donatelli) List(Liz, Pelletier) List(Cynthia, Arntzen) List(Jeremy, Farry) List(Charles, Crestani) List(Melanie, Seite) List(Lena, Radford) List(Andrew, Roberts) List(Nat, Gilpin) List(Sylvia, Foulston) List(Barry, Blumstein) List(Anthony, Rawles) List(Anthony, Rawles) List(Allen, Rosenblatt) List(Doug, Jacobs) List(Michael, Chen) List(Dorris, liebe) List(Alejandro, Savely) List(Ross, DeVincentis) List(Michael, Paige) List(Emily, Grady) List(Darrin, Sayre) List(Roland, Fjeld) List(Lisa, Hazard) List(Benjamin, Venier) List(Bryan, Mills) List(Bryan, Mills) List(Liz, Thompson) List(Mike, Caudle) List(Allen, Armold) List(Zuschuss, Carroll) List(Zuschuss, Carroll) List(Joel, Eaton) List(Brian, Moss) List(Eudokia, Martin) List(Dave, Poirier) List(Chuck, Magee) List(Anthony, Johnson) List(Lauren, Leatherbury) List(Pamela, Coakley) List(Pamela, Coakley) List(Joel, Jenkins) List(Alan, Barnes) List(Rachel, Payne) List(Ross, Baird) List(Ross, Baird) List(Joseph, Airdo) List(Daniel, Lacy) List(Maribeth, Schnelling) List(Bryan, Spruell) List(Delfina, Latchford) List(Delfina, Latchford) List(Delfina, Latchford) List(Ken, Brennan) List(Tracy, Zic) List(Troy, Staebel) List(Rob, Dowd) List(Greg, Tran) List(Steve, Nguyen) List(Zuschuss, Carroll) List(Matthew, Grinstein) List(Theresa, Swint) List(Theresa, Swint) List(Ross, Baird) List(Bill, Tyler) List(Karen, Daniels) List(Naresj, Patel) List(Eric, Hoffmann) List(Eric, Hoffmann) List(Christine, Sundaresam) List(Hunter, Lopez) List(Kelly, Lampkin) List(Penelope, Sewall) List(Delfina, Latchford) List(Joel, Eaton) List(Linda, Southworth) List(Becky, Martin) List(Kean, Thornton) List(Patrick, Gardner) List(Patrick, Gardner) List(Ross, Baird) List(Maurice, Satty) List(Justin, Hirsh) List(Quincy, Jones) List(Logan, Currie) List(Roy, Collins) List(Henry, Goldwyn) List(Laurel, Workman) List(Laurel, Elliston) List(Aaron, Smayling) List(Lindsay, Williams) List(Valerie, Dominguez) List(Karen, Daniels) List(Adrian, Barton) List(Damala, Kotsonis) List(Irene, Maddox) List(Bill, Donatelli) List(Shirley, Daniels) List(Shirley, Daniels) List(Damala, Kotsonis) List(Maxwell, Schwartz) List(Corinna, Mitchell) List(Dionis, Lloyd) List(Jane, Waco) List(Tom, Boeckenhauer) List(Paul, Lucas) List(Chloris, Kastensmidt) List(Victoria, Brennan) List(Jesus, Ocampo) List(Anthony, Witt) List(Muhammed, Yedwab) List(Rick, Duston) List(Jeremy, Farry) List(Cynthia, Arntzen) List(Jas, O'Carroll) List(Jas, O'Carroll) List(Julie, Kriz) List(Jenna, Caffey) List(Clay, Ludtke) List(Hilary, Holden) List(Christina, DeMoss) List(Neola, Schneider) List(Robert, Barroso) List(Rob, Dowd) List(Sean, Braxton) List(Pamela, Stobb) List(Damala, Kotsonis) List(Damala, Kotsonis) List(Arthur, Gainer) Li

UDFs with iterator of Series to iterator of Series

In [0]:
def expensive_operation_to_compute_discount():
    return 0.05

In [0]:
@pandas_udf("float")
def compute_discounted_sales_price(iterator: Iterator[pd.Series]) ->Iterator[pd.Series]:
    
    discount = expensive_operation_to_compute_discount()
    
    for sales_price in iterator:
        yield sales_price - discount * sales_price

In [0]:
superstore_df.select('Product Name', 'Sales', 
                    compute_discounted_sales_price('Sales').alias('Discounted Sales')).display()

Product Name Sales Discounted Sales Global Deluxe Stacking Chair, Gray 71.372 67.8034 Acco Pressboard Covers with Storage Hooks, 14 7/8" x 11", Executive Red 6.858 6.5151 Eldon Base for stackable storage shelf, platinum 77.88 73.986 Advantus 10-Drawer Portable Organizer, Chrome Metal Frame, Smoke Drawers 95.616 90.8352 Gould Plastics 9-Pocket Panel Bin, 18-3/8w x 5-1/4d x 20-1/2h, Black 211.96 201.362 Longer-Life Soft White Bulbs 6.16 5.852 Snap-A-Way Black Print Carbonless Ruled Speed Letter, Triplicate 75.88 72.086 Eldon Expressions Desk Accessory, Wood Pencil Holder, Oak 19.3 18.335 Avery Heavy-Duty EZD Binder With Locking Rings 16.74 15.903 Artistic Insta-Plaque 47.04 44.688 Xerox 1883 105.52 100.244 Tenex Personal Project File with Scoop Front Design, Black 80.88 76.836 Tenex File Box, Personal Filing Tote with Lid, Black 24.816 23.5752 SanDisk Ultra 32 GB MicroSDHC Class 10 Memory Card 176.8 167.96 Southworth 25% Cotton Antique Laid Paper & Envelopes 20.016 19.0152 Xerox 205 51.84 49.248 Wirebound Message Books, 5-1/2 x 4 Forms, 2 or 4 Forms per Page 16.056 15.2532 Nortel Business Series Terminal T7208 Digital phone 444.768 422.5296 Ibico Standard Transparent Covers 19.776 18.7872 Staple-based wall hangings 11.688 11.1036 Wirebound Message Books, Two 4 1/4" x 5" Forms per Page 7.61 7.2295 Belkin 19" Vented Equipment Shelf, Black 82.368 78.2496 Tenex Personal Project File with Scoop Front Design, Black 53.92 51.224 Xerox WorkCentre 6505DN Laser Multifunction Printer 2519.958 2393.9602 Quartet Omega Colored Chalk, 12/Pack 14.016 13.3152 Bevis Round Bullnose 29" High Table Top 1038.84 986.898 Acco 7-Outlet Masterpiece Power Center, Wihtout Fax/Phone Line Protection 194.528 184.8016 Premier Automatic Letter Opener 961.48 913.406 Advantus SlideClip Paper Clips 19.096 18.1412 GBC Premium Transparent Covers with Diagonal Lined Pattern 37.764 35.8758 Wilson Jones Custom Binder Spines & Labels 4.896 4.6512 Newell 314 17.856 16.9632 Anker 36W 4-Port USB Wall Charger Travel Power Adapter for iPhone 5s 5c 5 47.976 45.5772 Gould Plastics 9-Pocket Panel Bin, 18-3/8w x 5-1/4d x 20-1/2h, Black 211.96 201.362 3M Hangers With Command Adhesive 2.96 2.812 Logitech LS21 Speaker System - PC Multimedia - 2.1-CH - Wired 39.98 37.981 Wilson Jones Century Plastic Molded Ring Binders 12.462 11.8389 Xerox 1974 9.568 9.0896 Sony 64GB Class 10 Micro SDHC R40 Memory Card 179.95 170.9525 Novimex High-Tech Fabric Mesh Task Chair 113.568 107.8896 Westinghouse Mesh Shade Clip-On Gooseneck Lamp, Black 56.56 53.732 Epson WorkForce WF-2530 All-in-One Printer, Copier Scanner 69.99 66.4905 GE General Purpose, Extra Long Life, Showcase & Floodlight Incandescent Bulbs 2.91 2.7645 Chromcraft Rectangular Conference Tables 284.364 270.1458 Memorex Mini Travel Drive 16 GB USB 2.0 Flash Drive 63.88 60.686 Eldon Wave Desk Accessories 23.56 22.382 Decoflex Hanging Personal Folder File, Blue 92.52 87.894 Electrix 20W Halogen Replacement Bulb for Zoom-In Desk Lamp 40.2 38.19 Imation USB 2.0 Swivel Flash Drive USB flash drive - 4 GB - Pink 9.09 8.6355 Fellowes Officeware Wire Shelving 449.15 426.6925 Strathmore #10 Envelopes, Ultimate White 105.42 100.149 Premium Writing Pencils, Soft, #2 by Central Association for the Blind 7.152 6.7944 Imation 16GB Mini TravelDrive USB 2.0 Flash Drive 66.26 62.947 Panasonic KX-TG9471B 979.95 930.9525 Cardinal Poly Pocket Divider Pockets for Ring Binders 10.752 10.2144 Eureka The Boss Cordless Rechargeable Stick Vac 152.94 145.293 Fellowes Officeware Wire Shelving 646.776 614.4372 Deflect-o EconoMat Studded, No Bevel Mat for Low Pile Carpeting 66.112 62.8064 HON 5400 Series Task Chairs for Big and Tall 1121.568 1065.4896 GBC Prepunched Paper, 19-Hole, for Binding Systems, 24-lb 84.056 79.8532 Advantus Panel Wall Acrylic Frame 13.128 12.4716 Alliance Big Bands Rubber Bands, 12/Pack 3.96 3.762 Martin-Yale Premier Letter Opener 51.52 48.944 Newell 312 9.344 8.8768 AT&T 1070 Corded Phone 445.96 423.662 Angle-D Ring Binders 3.282 3.1179 DAX V

UDFs iterator of multiple series to iterator of series

In [0]:
@pandas_udf("string")
def combine_city_state(iterator: Iterator[Tuple[pd.Series, pd.Series]]) -> Iterator[pd.Series]:
    for city, state in iterator:
        yield city + ' (' + state + ')'

In [0]:
superstore_df.select('City', 'State', combine_city_state('City', 'State').alias('City (State)')).display()

City State City (State) Philadelphia Pennsylvania Philadelphia (Pennsylvania) Philadelphia Pennsylvania Philadelphia (Pennsylvania) Los Angeles California Los Angeles (California) Melbourne Florida Melbourne (Florida) Westland Michigan Westland (Michigan) New Albany Indiana New Albany (Indiana) Springfield Virginia Springfield (Virginia) Houston Texas Houston (Texas) Decatur Alabama Decatur (Alabama) Wilmington Delaware Wilmington (Delaware) San Jose California San Jose (California) San Jose California San Jose (California) Decatur Illinois Decatur (Illinois) Los Angeles California Los Angeles (California) Grand Prairie Texas Grand Prairie (Texas) New York City New York New York City (New York) Philadelphia Pennsylvania Philadelphia (Pennsylvania) Whittier California Whittier (California) Dublin Ohio Dublin (Ohio) Chicago Illinois Chicago (Illinois) San Diego California San Diego (California) Chicago Illinois Chicago (Illinois) Chicago Illinois Chicago (Illinois) Houston Texas Houston (Texas) Chapel Hill North Carolina Chapel Hill (North Carolina) Los Angeles California Los Angeles (California) Tamarac Florida Tamarac (Florida) Tamarac Florida Tamarac (Florida) Columbus Ohio Columbus (Ohio) Philadelphia Pennsylvania Philadelphia (Pennsylvania) Philadelphia Pennsylvania Philadelphia (Pennsylvania) Philadelphia Pennsylvania Philadelphia (Pennsylvania) San Francisco California San Francisco (California) San Francisco California San Francisco (California) Philadelphia Pennsylvania Philadelphia (Pennsylvania) New York City New York New York City (New York) Peoria Illinois Peoria (Illinois) Miami Florida Miami (Florida) San Francisco California San Francisco (California) San Francisco California San Francisco (California) Lawrence Massachusetts Lawrence (Massachusetts) New Rochelle New York New Rochelle (New York) Columbus Indiana Columbus (Indiana) Akron Ohio Akron (Ohio) Norman Oklahoma Norman (Oklahoma) Phoenix Arizona Phoenix (Arizona) San Francisco California San Francisco (California) Troy New York Troy (New York) San Diego California San Diego (California) Rochester New York Rochester (New York) Fayetteville Arkansas Fayetteville (Arkansas) Newark Ohio Newark (Ohio) Los Angeles California Los Angeles (California) Montgomery Alabama Montgomery (Alabama) New York City New York New York City (New York) Henderson Kentucky Henderson (Kentucky) Springfield Ohio Springfield (Ohio) Fort Worth Texas Fort Worth (Texas) San Francisco California San Francisco (California) San Francisco California San Francisco (California) Tampa Florida Tampa (Florida) Seattle Washington Seattle (Washington) Los Angeles California Los Angeles (California) Laredo Texas Laredo (Texas) San Diego California San Diego (California) Philadelphia Pennsylvania Philadelphia (Pennsylvania) New York City New York New York City (New York) Dearborn Michigan Dearborn (Michigan) Sierra Vista Arizona Sierra Vista (Arizona) Vancouver Washington Vancouver (Washington) Vancouver Washington Vancouver (Washington) New York City New York New York City (New York) New York City New York New York City (New York) Jackson Mississippi Jackson (Mississippi) Cleveland Ohio Cleveland (Ohio) Seattle Washington Seattle (Washington) Los Angeles California Los Angeles (California) Detroit Michigan Detroit (Michigan) Oceanside New York Oceanside (New York) Seattle Washington Seattle (Washington) Trenton Michigan Trenton (Michigan) Columbus Ohio Columbus (Ohio) Des Moines Iowa Des Moines (Iowa) Columbus Ohio Columbus (Ohio) Columbus Ohio Columbus (Ohio) Lancaster California Lancaster (California) Monroe Louisiana Monroe (Louisiana) Omaha Nebraska Omaha (Nebraska) Edmonds Washington Edmonds (Washington) Edmonds Washington Edmonds (Washington) Florence Kentucky Florence (Kentucky) New York City New York New York City (New York) Los Angeles California Los Angeles (California) Salinas California Salinas (California) San Francisco California San Francisco (California) Jacksonville Florida Jackson

In [0]:
@pandas_udf("float")
def compute_cost(iterator: Iterator[Tuple[pd.Series, pd.Series]]) -> Iterator[pd.Series]:
    for sales, profit in iterator:
        yield sales - profit

In [0]:
superstore_df.select('Product Name', 'Sales', 'Profit', compute_cost('Sales', 'Profit').alias('Cost')).display()

Product Name Sales Profit Cost Global Deluxe Stacking Chair, Gray 71.372 -1.0196 72.3916 Acco Pressboard Covers with Storage Hooks, 14 7/8" x 11", Executive Red 6.858 -5.715 12.573 Eldon Base for stackable storage shelf, platinum 77.88 3.894 73.986 Advantus 10-Drawer Portable Organizer, Chrome Metal Frame, Smoke Drawers 95.616 9.5616 86.0544 Gould Plastics 9-Pocket Panel Bin, 18-3/8w x 5-1/4d x 20-1/2h, Black 211.96 8.4784 203.4816 Longer-Life Soft White Bulbs 6.16 2.9568 3.2032 Snap-A-Way Black Print Carbonless Ruled Speed Letter, Triplicate 75.88 35.6636 40.2164 Eldon Expressions Desk Accessory, Wood Pencil Holder, Oak 19.3 -14.475 33.775 Avery Heavy-Duty EZD Binder With Locking Rings 16.74 8.0352 8.7048 Artistic Insta-Plaque 47.04 18.3456 28.6944 Xerox 1883 105.52 48.5392 56.9808 Tenex Personal Project File with Scoop Front Design, Black 80.88 21.0288 59.8512 Tenex File Box, Personal Filing Tote with Lid, Black 24.816 1.8612 22.9548 SanDisk Ultra 32 GB MicroSDHC Class 10 Memory Card 176.8 22.984 153.816 Southworth 25% Cotton Antique Laid Paper & Envelopes 20.016 6.255 13.761 Xerox 205 51.84 24.8832 26.9568 Wirebound Message Books, 5-1/2 x 4 Forms, 2 or 4 Forms per Page 16.056 5.8203 10.2357 Nortel Business Series Terminal T7208 Digital phone 444.768 44.4768 400.2912 Ibico Standard Transparent Covers 19.776 -13.8432 33.6192 Staple-based wall hangings 11.688 -4.6752 16.3632 Wirebound Message Books, Two 4 1/4" x 5" Forms per Page 7.61 3.5767 4.0333 Belkin 19" Vented Equipment Shelf, Black 82.368 -19.5624 101.9304 Tenex Personal Project File with Scoop Front Design, Black 53.92 4.044 49.876 Xerox WorkCentre 6505DN Laser Multifunction Printer 2519.958 -251.9958 2771.9539 Quartet Omega Colored Chalk, 12/Pack 14.016 4.7304 9.2856 Bevis Round Bullnose 29" High Table Top 1038.84 51.942 986.898 Acco 7-Outlet Masterpiece Power Center, Wihtout Fax/Phone Line Protection 194.528 24.316 170.212 Premier Automatic Letter Opener 961.48 -204.3145 1165.7946 Advantus SlideClip Paper Clips 19.096 6.6836 12.4124 GBC Premium Transparent Covers with Diagonal Lined Pattern 37.764 -27.6936 65.4576 Wilson Jones Custom Binder Spines & Labels 4.896 -3.4272 8.3232 Newell 314 17.856 1.116 16.74 Anker 36W 4-Port USB Wall Charger Travel Power Adapter for iPhone 5s 5c 5 47.976 4.7976 43.1784 Gould Plastics 9-Pocket Panel Bin, 18-3/8w x 5-1/4d x 20-1/2h, Black 211.96 8.4784 203.4816 3M Hangers With Command Adhesive 2.96 0.777 2.183 Logitech LS21 Speaker System - PC Multimedia - 2.1-CH - Wired 39.98 13.5932 26.3868 Wilson Jones Century Plastic Molded Ring Binders 12.462 -20.5623 33.0243 Xerox 1974 9.568 3.4684 6.0996 Sony 64GB Class 10 Micro SDHC R40 Memory Card 179.95 37.7895 142.1605 Novimex High-Tech Fabric Mesh Task Chair 113.568 -18.4548 132.0228 Westinghouse Mesh Shade Clip-On Gooseneck Lamp, Black 56.56 14.7056 41.8544 Epson WorkForce WF-2530 All-in-One Printer, Copier Scanner 69.99 30.0957 39.8943 GE General Purpose, Extra Long Life, Showcase & Floodlight Incandescent Bulbs 2.91 1.3677 1.5423 Chromcraft Rectangular Conference Tables 284.364 -75.8304 360.1944 Memorex Mini Travel Drive 16 GB USB 2.0 Flash Drive 63.88 24.9132 38.9668 Eldon Wave Desk Accessories 23.56 7.068 16.492 Decoflex Hanging Personal Folder File, Blue 92.52 24.9804 67.5396 Electrix 20W Halogen Replacement Bulb for Zoom-In Desk Lamp 40.2 19.296 20.904 Imation USB 2.0 Swivel Flash Drive USB flash drive - 4 GB - Pink 9.09 1.9089 7.1811 Fellowes Officeware Wire Shelving 449.15 8.983 440.167 Strathmore #10 Envelopes, Ultimate White 105.42 51.6558 53.7642 Premium Writing Pencils, Soft, #2 by Central Association for the Blind 7.152 0.7152 6.4368 Imation 16GB Mini TravelDrive USB 2.0 Flash Drive 66.26 27.1666 39.0934 Panasonic KX-TG9471B 979.95 274.386 705.564 Cardinal Poly Pocket Divider Pockets for Ring Binders 10.752 3.36 7.392 Eureka The Boss Cordless Rechargeable Stick Vac 152.94 41.2938 111.6462 Fellowes Officeware Wire Shelving 646.776 -145.5246 792.3006 Deflect-o EconoMat Studded, No

In [0]:
# use within the SQL queries as usual UDFs

spark.udf.register('compute_cost', compute_cost)
superstore_df.createOrReplaceTempView('superstore_data')
spark.sql("""select 'Product Name', Sales, Profit, compute_cost(Sales, Profit) as Cost
            from superstore_data""").display()

Product Name Sales Profit Cost Product Name 71.372 -1.0196 72.3916 Product Name 6.858 -5.715 12.573 Product Name 77.88 3.894 73.986 Product Name 95.616 9.5616 86.0544 Product Name 211.96 8.4784 203.4816 Product Name 6.16 2.9568 3.2032 Product Name 75.88 35.6636 40.2164 Product Name 19.3 -14.475 33.775 Product Name 16.74 8.0352 8.7048 Product Name 47.04 18.3456 28.6944 Product Name 105.52 48.5392 56.9808 Product Name 80.88 21.0288 59.8512 Product Name 24.816 1.8612 22.9548 Product Name 176.8 22.984 153.816 Product Name 20.016 6.255 13.761 Product Name 51.84 24.8832 26.9568 Product Name 16.056 5.8203 10.2357 Product Name 444.768 44.4768 400.2912 Product Name 19.776 -13.8432 33.6192 Product Name 11.688 -4.6752 16.3632 Product Name 7.61 3.5767 4.0333 Product Name 82.368 -19.5624 101.9304 Product Name 53.92 4.044 49.876 Product Name 2519.958 -251.9958 2771.9539 Product Name 14.016 4.7304 9.2856 Product Name 1038.84 51.942 986.898 Product Name 194.528 24.316 170.212 Product Name 961.48 -204.3145 1165.7946 Product Name 19.096 6.6836 12.4124 Product Name 37.764 -27.6936 65.4576 Product Name 4.896 -3.4272 8.3232 Product Name 17.856 1.116 16.74 Product Name 47.976 4.7976 43.1784 Product Name 211.96 8.4784 203.4816 Product Name 2.96 0.777 2.183 Product Name 39.98 13.5932 26.3868 Product Name 12.462 -20.5623 33.0243 Product Name 9.568 3.4684 6.0996 Product Name 179.95 37.7895 142.1605 Product Name 113.568 -18.4548 132.0228 Product Name 56.56 14.7056 41.8544 Product Name 69.99 30.0957 39.8943 Product Name 2.91 1.3677 1.5423 Product Name 284.364 -75.8304 360.1944 Product Name 63.88 24.9132 38.9668 Product Name 23.56 7.068 16.492 Product Name 92.52 24.9804 67.5396 Product Name 40.2 19.296 20.904 Product Name 9.09 1.9089 7.1811 Product Name 449.15 8.983 440.167 Product Name 105.42 51.6558 53.7642 Product Name 7.152 0.7152 6.4368 Product Name 66.26 27.1666 39.0934 Product Name 979.95 274.386 705.564 Product Name 10.752 3.36 7.392 Product Name 152.94 41.2938 111.6462 Product Name 646.776 -145.5246 792.3006 Product Name 66.112 -84.2928 150.4048 Product Name 1121.568 0.0 1121.568 Product Name 84.056 27.3182 56.7378 Product Name 13.128 3.7743 9.3537 Product Name 3.96 0.0 3.96 Product Name 51.52 1.5456 49.9744 Product Name 9.344 1.168 8.176 Product Name 445.96 55.745 390.215 Product Name 3.282 -2.6256 5.9076 Product Name 9.94 3.0814 6.8586 Product Name 555.21 178.901 376.309 Product Name 30.144 3.0144 27.1296 Product Name 14.8 6.068 8.732 Product Name 316.0 31.6 284.4 Product Name 103.12 10.312 92.808 Product Name 68.6 18.522 50.078 Product Name 19.44 9.3312 10.1088 Product Name 15.072 4.1448 10.9272 Product Name 209.88 35.6796 174.2004 Product Name 146.82 73.41 73.41 Product Name 1652.94 231.4116 1421.5284 Product Name 33.63 10.089 23.541 Product Name 18.72 6.552 12.168 Product Name 157.74 56.7864 100.9536 Product Name 107.982 -26.9955 134.9775 Product Name 34.58 14.5236 20.0564 Product Name 32.07 -22.449 54.519 Product Name 35.49 -15.6156 51.1056 Product Name 348.928 34.8928 314.0352 Product Name 12.96 6.2208 6.7392 Product Name 28.4 11.076 17.324 Product Name 11.52 3.2256 8.2944 Product Name 25.78 2.578 23.202 Product Name 180.66 50.5848 130.0752 Product Name 186.048 9.3024 176.7456 Product Name 14.62 6.8714 7.7486 Product Name 38.88 18.6624 20.2176 Product Name 7.36 0.1472 7.2128 Product Name 59.184 5.1786 54.0054 Product Name 17.46 5.9364 11.5236 Product Name 155.82 42.0714 113.7486 Product Name 70.008 24.5028 45.5052 Product Name 46.2 12.936 33.264 Product Name 89.856 21.3408 68.5152 Product Name 12.96 6.2208 6.7392 Product Name 2065.32 -619.596 2684.916 Product Name 15.552 5.4432 10.1088 Product Name 4.752 -3.168 7.92 Product Name 204.6 53.196 151.404 Product Name 4.608 1.6704 2.9376 Product Name 12.96 6.2208 6.7392 Product Name 124.2 -31.05 155.25 Product Name 18.588 -13.6312 32.2192 Product Name 30.072 10.1493 19.9227 Product Name 34.02 16.6698 17.3502 Product Name 559.984 55.9984 503.9856 Product Name 14.624 5.484 9.14 Product Name 33.11 

Series to Scalar UDFs

In [0]:
@pandas_udf('float')
def average(values: pd.Series) -> float:
    return values.mean()

In [0]:
superstore_df.select(average('Sales').alias('Average Sales')).display()

Average Sales 229.858

In [0]:
@pandas_udf('float')
def median(values: pd.Series) -> float:
    return values.median()

In [0]:
superstore_df.select(median('Sales').alias('Median Sales')).display()

Median Sales 54.49

In [0]:
#use in SQL

spark.udf.register('average', average)
spark.sql('select average(profit) from superstore_data').display()

average(profit) 28.656897

In [0]:
spark.sql('select category, average(profit) from superstore_data group by category').display()

category average(profit) Furniture 8.699327 Office Supplies 20.32705 Technology 78.752